In [1]:
from sklearn.ensemble import RandomForestClassifier
import pandas as pd
import h5py
import numpy as np
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split 
import pywt
from plotly import tools
from plotly.offline import init_notebook_mode, iplot, plot
# import cufflinks as cf
import xgboost as xgb
import plotly.graph_objs as go
from datetime import datetime
from datetime import timedelta
import warnings
import time
from collections import Counter
import scipy
import pywt
warnings.filterwarnings('ignore')

from sklearn.preprocessing import LabelBinarizer

In [2]:
X_train = h5py.File("original_data/X_train.h5", "r")
y_train_ = pd.read_csv("original_data/y_train.csv").as_matrix()[:, 1].squeeze()
df_train = pd.DataFrame(data=X_train["features"][:])

In [3]:
X_test = h5py.File("original_data/X_test.h5", "r") #we don't really care about that for now
df_test = pd.DataFrame(data=X_test["features"][:])

In [3]:
def label_columns(df):
    l_columns = ['num_pso', 
             'mean_amp_pso',
             'mean_dur_pso',
              'amp_cso',
              'dur_cso',
              'curr_sleep_stage',
              'time_since_sleep',
              'time_in_ds',
              'time_in_ls',
              'time_in_rs',
              'time_in_ws']
    for i in range(12, 1261+1):
        l_columns.append('eeg_signal_%s'%(i-12+1))
    df.columns = l_columns

    return df

df_train=label_columns(df_train)
#df_test=label_columns(df_test)

## Getting spindles [done]

In [ ]:
import yasa
import numpy as np
import pandas as pd
import seaborn as sns1
import logging
logging.getLogger("imported_module").setLevel(logging.ERROR)

sf = 125.
data = df_train.loc[:, 'eeg_signal_1':]
data.loc[0]
#df_train.loc[:, 'eeg_signal_1':].apply(lambda x: perm_entropy(x, order=3, normalize=True), axis=1)
sp = yasa.spindles_detect(data.loc[1], sf)
# isinstance(sp, pd.DataFrame):
sp

In [ ]:
#1 if spindles else 0
df_train_final['spindles'] = data.apply(lambda x: 1 if isinstance(yasa.spindles_detect(x, sf), pd.DataFrame) else 0, axis=1)

03-Dec-19 23:45:58 | WARNING | No spindles were found in data. Returning None.
03-Dec-19 23:45:58 | WARNING | No spindles were found in data. Returning None.
03-Dec-19 23:45:58 | WARNING | No spindles were found in data. Returning None.
03-Dec-19 23:45:58 | WARNING | No spindles were found in data. Returning None.
03-Dec-19 23:45:58 | WARNING | No spindles were found in data. Returning None.
03-Dec-19 23:45:58 | WARNING | No spindles were found in data. Returning None.
03-Dec-19 23:45:58 | WARNING | No spindles were found in data. Returning None.
03-Dec-19 23:45:58 | WARNING | No spindles were found in data. Returning None.
03-Dec-19 23:45:58 | WARNING | No spindles were found in data. Returning None.
03-Dec-19 23:45:58 | WARNING | No spindles were found in data. Returning None.
03-Dec-19 23:45:58 | WARNING | No spindles were found in data. Returning None.
03-Dec-19 23:45:58 | WARNING | No spindles were found in data. Returning None.
03-Dec-19 23:45:58 | WARNING | No spindles were foun

In [17]:
df_train_final.to_hdf('df_train_final.h5', key='df_train_final')

In [19]:
df_train_final.groupby(['spindles']).count()

num_pso  mean_amp_pso  mean_dur_pso  amp_cso  dur_cso  \
spindles                                                          
0          258666        258666        258666   258666   258666   
1            2968          2968          2968     2968     2968   

          time_since_sleep  time_in_ds  time_in_ls  time_in_rs  time_in_ws  \
spindles                                                                     
0                   258666      258666      258666      258666      258666   
1                     2968        2968        2968        2968        2968   

          ...  wawelets_86  wawelets_87  wawelets_88  wawelets_89  \
spindles  ...                                                       
0         ...       258666       258666       258666       258666   
1         ...         2968         2968         2968         2968   

          wawelets_90  wawelets_91  wawelets_92  wawelets_93  wawelets_94  \
spindles                                                                    
0              258666       258666       258666       258666       258666   
1                2968         2968         2968         2968         2968   

          wawelets_95  
spindles               
0              258666  
1                2968  

[2 rows x 181 columns]

## Getting Slow waves

In [8]:
# number of slow oscillations
sf = 125
data = df_train.loc[:, 'eeg_signal_1':]

sw = yasa.sw_detect(data.loc[1], sf)
sw

Start  NegPeak  MidCrossing  PosPeak    End  Duration  ValNegPeak  \
0  1.576    1.728        2.088    2.256  2.800     1.224  -73.233544   
1  9.168    9.336        9.496    9.744  9.944     0.776  -59.113869   

   ValPosPeak         PTP       Slope  Frequency  
0   41.345971  114.579515  318.276429   0.816993  
1   51.000679  110.114548  688.215922   1.288660

In [9]:
df_train_final['num_SO_detected'] = data.apply(lambda x: len(yasa.sw_detect(x, sf)) if isinstance(yasa.sw_detect(x, sf), pd.DataFrame) else 0, axis=1)

09-Dec-19 21:39:07 | WARNING | No slow-wave satisfying all criteria. Returning None.
09-Dec-19 21:39:07 | WARNING | No slow-wave satisfying all criteria. Returning None.
09-Dec-19 21:39:07 | WARNING | No slow-wave satisfying all criteria. Returning None.
09-Dec-19 21:39:07 | WARNING | No slow-wave satisfying all criteria. Returning None.
09-Dec-19 21:39:07 | WARNING | No slow-wave satisfying all criteria. Returning None.
09-Dec-19 21:39:08 | WARNING | No slow-wave satisfying all criteria. Returning None.
09-Dec-19 21:39:08 | WARNING | No slow-wave satisfying all criteria. Returning None.
09-Dec-19 21:39:08 | WARNING | No slow-wave satisfying all criteria. Returning None.
09-Dec-19 21:39:08 | WARNING | No slow-wave satisfying all criteria. Returning None.
09-Dec-19 21:39:08 | WARNING | No slow-wave satisfying all criteria. Returning None.
09-Dec-19 21:39:08 | WARNING | No slow-wave satisfying all criteria. Returning None.
09-Dec-19 21:39:08 | WARNING | No slow-wave satisfying all criter

In [11]:
df_train_final.groupby(['num_SO_detected']).count().num_pso

num_SO_detected
0     47385
1     72209
2     56703
3     39369
4     24618
5     13015
6      5647
7      2036
8       536
9        96
10       19
11        1
Name: num_pso, dtype: int64

In [12]:
df_train_final.to_hdf('df_train_final.h5', key='df_train_final')

In [45]:
df_train_final['num_SO_detected'] = df_train_final['num_SO_detected'].astype(int)

In [46]:
means = df_train_final.groupby('num_SO_detected')[var_to_pred].mean()
means

num_SO_detected
0     0.557582
1     0.682851
2     0.845564
3     0.993853
4     1.111544
5     1.195236
6     1.280503
7     1.342829
8     1.345149
9     1.531250
10    1.473684
11    1.000000
Name: SO, dtype: float64

In [47]:
df_train_final['num_SO_detected'] = df_train_final['num_SO_detected'].map(means)

## Dummy variables target encoding

In [5]:
df_train.columns

Index(['num_pso', 'mean_amp_pso', 'mean_dur_pso', 'amp_cso', 'dur_cso',
       'curr_sleep_stage', 'time_since_sleep', 'time_in_ds', 'time_in_ls',
       'time_in_rs',
       ...
       'eeg_signal_1241', 'eeg_signal_1242', 'eeg_signal_1243',
       'eeg_signal_1244', 'eeg_signal_1245', 'eeg_signal_1246',
       'eeg_signal_1247', 'eeg_signal_1248', 'eeg_signal_1249',
       'eeg_signal_1250'],
      dtype='object', length=1261)

In [2]:
df_train_final['curr_sleep_stage'] = df_train['curr_sleep_stage']

NameError: name 'df_train' is not defined

In [3]:
means = df_train_final.groupby('curr_sleep_stage')[var_to_pred].mean()
means

NameError: name 'df_train_final' is not defined

In [ ]:
df_train_final['curr_sleep_stage'] = df_train_final['curr_sleep_stage'].map(means)

In [73]:
df_train_final.to_hdf('df_train_final.h5', key='df_train_final')

## Data collection and models definition

In [4]:
df_train_final = pd.read_hdf('df_train_final.h5', 'df_train_final')

In [7]:
df_signal=df_train.loc[:, 'eeg_signal_1':'eeg_signal_1250']
t=np.linspace(0,10,1250)
df_signal.iloc[9,:]

eeg_signal_1       68.523425
eeg_signal_2       71.477495
eeg_signal_3       73.694816
eeg_signal_4       72.391170
eeg_signal_5       67.268982
eeg_signal_6       60.707611
eeg_signal_7       57.939798
eeg_signal_8       58.474464
eeg_signal_9       60.401210
eeg_signal_10      59.667061
eeg_signal_11      56.288727
eeg_signal_12      50.228196
eeg_signal_13      45.059911
eeg_signal_14      44.371651
eeg_signal_15      44.353494
eeg_signal_16      42.270068
eeg_signal_17      39.093997
eeg_signal_18      40.008072
eeg_signal_19      44.785237
eeg_signal_20      52.197293
eeg_signal_21      63.241019
eeg_signal_22      74.207808
eeg_signal_23      80.068246
eeg_signal_24      80.399927
eeg_signal_25      78.025620
eeg_signal_26      70.148884
eeg_signal_27      57.849000
eeg_signal_28      44.059759
eeg_signal_29      31.791982
eeg_signal_30      24.245383
                     ...    
eeg_signal_1221    18.434791
eeg_signal_1222    21.326089
eeg_signal_1223    23.011575
eeg_signal_122

In [7]:
equations = {
  
     'base_model': {'predictors': list(df_train_final.columns)[0:13]},
     'entropy_fft': {'predictors': list(df_train_final.columns[0:81])},
     'dummy_variables_only': {'predictors': list(df_train_final.columns)[0:11]+list(df_train_final.columns)[81:83]},
     'dummy_variables': {'predictors': list(df_train_final.columns)[0:83]},
     'dummy_variables_target_encoding': {'predictors':list(df_train_final.columns)[0:81] + [df_train_final.columns[-1]]},
    
     'wawelets': {'predictors': list(df_train_final.columns[0:17])+list(df_train_final.columns[85:181])},
     #'wawelets_spindles':{'predictors': list(df_train_final.columns[0:17])+list(df_train_final.columns[85:182])},
     'wawelets_target_encoding': {'predictors': list(df_train_final.columns[0:17])+list(df_train_final.columns[85:181])
                                  + [df_train_final.columns[-1]]},
     'wawelets_dummies': {'predictors': list(df_train_final.columns[0:17])+list(df_train_final.columns[81:83])
                                  + list(df_train_final.columns[85:181])},
     'wawelets_SO_detected': {'predictors': list(df_train_final.columns[0:17])+list(df_train_final.columns[81:83])
                                  + list(df_train_final.columns[85:181]) + [df_train_final.columns[-1]]},

     'fft_wawelets' : {'predictors': list(df_train_final.columns[0:81])+list(df_train_final.columns[85:181])},
     #'fft_wawelets_spindles': {'predictors': list(df_train_final.columns[0:81])+list(df_train_final.columns[85:182])},

#fft_2_sec
     'entropy_fft_2_sec':{'predictors': list(df_train_final.columns)[0:17] +list(df_train_final.columns)[183:246]}, 
     'fft_2_sec_wavelets':{'predictors': list(df_train_final.columns)[0:17] + list(df_train_final.columns[85:181]) +
                           list(df_train_final.columns)[183:246]},
     'fft_fft_2_sec_wavelets':{'predictors': list(df_train_final.columns)[0:81] + list(df_train_final.columns[85:181]) +
                           list(df_train_final.columns)[183:246]},

#wavelets_2_sec
    'wawelets_2_sec':{'predictors': list(df_train_final.columns)[0:17] +list(df_train_final.columns)[246:306]}, 
    'wavelets_wavelets_2_sec': {'predictors': list(df_train_final.columns)[0:17]  + list(df_train_final.columns[85:181]) 
                                + list(df_train_final.columns)[246:306]},
    
    'fft_wawelets_2_sec':{'predictors': list(df_train_final.columns)[0:81] +list(df_train_final.columns)[246:306]}, 
    'fft_2_sec_wawelets_2_sec':{'predictors': list(df_train_final.columns)[0:17] +list(df_train_final.columns)[183:306]},
    'fft_fft_2_sec_wawelets_2_sec':{'predictors': list(df_train_final.columns)[0:81] + list(df_train_final.columns)[183:306]}, 
    
    'fft_fft_2_sec_wawelets_wawelets_2_sec':{'predictors': list(df_train_final.columns)[0:81] + list(df_train_final.columns[85:181]) 
                                             +list(df_train_final.columns)[183:306]},
}

cols_eq = list(equations.keys())

In [8]:
var_to_pred = 'SO'

In [8]:
X_train, X_val, y_train, y_val = train_test_split(df_train_final.loc[:, df_train_final.columns != var_to_pred], df_train_final[var_to_pred], test_size=0.10,random_state=0, stratify=df_train_final[var_to_pred])

In [9]:
y_train = pd.DataFrame(y_train)
y_val = pd.DataFrame(y_val)

## Models

In [53]:
### Number of SO detected

model='wawelets_SO_detected'
predictors = equations[model]['predictors']
print(predictors)

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

['num_pso', 'mean_amp_pso', 'mean_dur_pso', 'amp_cso', 'dur_cso', 'time_since_sleep', 'time_in_ds', 'time_in_ls', 'time_in_rs', 'time_in_ws', 'mean', 'max', 'min', 'perm_entropy', 'svd_entropy', 'higuchi_fd', 'detrended_fluctuation', 'curr_sleep_stage_2.0', 'curr_sleep_stage_3.0', 'wawelets_0', 'wawelets_1', 'wawelets_2', 'wawelets_3', 'wawelets_4', 'wawelets_5', 'wawelets_6', 'wawelets_7', 'wawelets_8', 'wawelets_9', 'wawelets_10', 'wawelets_11', 'wawelets_12', 'wawelets_13', 'wawelets_14', 'wawelets_15', 'wawelets_16', 'wawelets_17', 'wawelets_18', 'wawelets_19', 'wawelets_20', 'wawelets_21', 'wawelets_22', 'wawelets_23', 'wawelets_24', 'wawelets_25', 'wawelets_26', 'wawelets_27', 'wawelets_28', 'wawelets_29', 'wawelets_30', 'wawelets_31', 'wawelets_32', 'wawelets_33', 'wawelets_34', 'wawelets_35', 'wawelets_36', 'wawelets_37', 'wawelets_38', 'wawelets_39', 'wawelets_40', 'wawelets_41', 'wawelets_42', 'wawelets_43', 'wawelets_44', 'wawelets_45', 'wawelets_46', 'wawelets_47', 'wawelet

0.5199892982724355

#### Dummy variables

In [51]:
model='dummy_variables'
predictors = equations[model]['predictors']

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

0.5127656321663354

In [52]:
model='dummy_variables_target_encoding'
predictors = equations[model]['predictors']

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

0.5127656321663354

In [11]:
import boostparam #external python file to hypertune xgboost model
from importlib import reload
reload(boostparam)

df = pd.concat([X_train,y_train], axis=1)

In [ ]:
model='wawelets'
predictors = equations[model]['predictors']

eval_metric =  'error'
scoring = 'accuracy'

params = boostparam.tune_all_hyper_params(df, predictors, var_to_pred, eval_metric, scoring, seed = 6)
model = xgboost.XGBClassifier(**params)
model.fit(df[predictors], df[var_to_pred])
xgboost.plot_importance(model)
y_pred = model.predict(X_test)

accuracy_score(y_val, y_pred)

seak best n n_est
use TrainCV: True
n_estimators: 30


In [ ]:
import shap
shap.initjs()

In [67]:
model='wawelets_dummies'
predictors = equations[model]['predictors']

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

0.5224736278856444

In [ ]:
model='wawelets_dummies'
predictors = equations[model]['predictors']

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

In [11]:
with open("y_benchmark.csv", "w") as f:
    f.write("".join(["id,label\n"] + ["{},{}\n".format(i, y) for i, y in enumerate(y_pred)]))

#### All fft and wawelets models

In [14]:
model='fft_wawelets_spindles'
predictors = equations[model]['predictors']

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

0.5176196300259899

In [68]:
model='wawelets'
predictors = equations[model]['predictors']

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

0.5186133618712735

In [19]:
model='wawelets_spindles'
predictors = equations[model]['predictors']

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

0.5186133618712735

In [8]:
df_train_final.head()

num_pso  mean_amp_pso  mean_dur_pso     amp_cso  dur_cso  time_since_sleep  \
0    237.0    152.658761    341.523207  128.017491    429.0           11379.0   
1    176.0    146.883435    338.039773  119.130849    196.0            6721.0   
2    456.0    152.376541    335.629386  164.292580    417.0           26832.0   
3     21.0    139.720772    336.285714  159.237082    407.0            1289.0   
4     72.0    140.649432    349.875000  130.184278    297.0            2262.0   

   time_in_ds  time_in_ls  time_in_rs  time_in_ws  ...  wawelets_87  \
0      2730.0      3780.0         0.0       480.0  ...    -1.508171   
1      2580.0      2100.0         0.0       480.0  ...    -1.302524   
2      3240.0      7440.0      2130.0       750.0  ...    -1.774095   
3         0.0        60.0         0.0       450.0  ...    -1.514035   
4       630.0       960.0         0.0       450.0  ...    -1.425063   

   wawelets_88  wawelets_89  wawelets_90  wawelets_91  wawelets_92  \
0    -0.600457     0.605929     1.524894     0.011170    -0.000105   
1    -0.578372     0.553759     1.361592    -0.032801     0.001091   
2    -0.736667     0.757092     1.778728     0.016140    -0.001139   
3    -0.667986     0.661924     1.535148    -0.005341     0.000916   
4    -0.590922     0.636247     1.404894     0.001580    -0.002912   

   wawelets_93  wawelets_94  wawelets_95  spindles  
0     1.006676     1.013396     0.740114         0  
1     0.845156     0.714289     0.661250         1  
2     1.099851     1.209672     0.872444         0  
3     0.961756     0.924975     0.773179         0  
4     0.872183     0.760704     0.701210         0  

[5 rows x 182 columns]

## Focus sur la puissance spectrale (FFT) sur uniquement les 2 dernières secondes

In [7]:
df_train.loc[:, 'eeg_signal_1000':].head()

eeg_signal_1000  eeg_signal_1001  eeg_signal_1002  eeg_signal_1003  \
0        72.628265        78.278013        82.572335        81.424997   
1        -3.325843        -4.675120        -8.396188       -12.052140   
2        28.786824        29.389482        25.798998        22.223248   
3       -18.513349       -21.943170       -24.796037       -22.642019   
4         6.836797         3.967112        -2.311266        -9.177676   

   eeg_signal_1004  eeg_signal_1005  eeg_signal_1006  eeg_signal_1007  \
0        76.538797        72.609733        67.776895        64.315412   
1       -13.369057       -13.227978       -11.215382        -8.591497   
2        21.287829        21.145861        23.593595        28.271680   
3       -16.852708       -11.350586        -6.346709        -1.758309   
4        -8.967269        -0.699526         8.098728        13.740305   

   eeg_signal_1008  eeg_signal_1009  ...  eeg_signal_1241  eeg_signal_1242  \
0        66.249871        68.837016  ...        22.707487        15.042639   
1        -2.498960         5.556113  ...         2.839801         3.458973   
2        31.723988        30.361499  ...        27.093293        22.821611   
3         1.277970         2.783182  ...        28.191571        25.032295   
4        14.133323        14.636480  ...        -7.942308       -10.407617   

   eeg_signal_1243  eeg_signal_1244  eeg_signal_1245  eeg_signal_1246  \
0         9.706864         7.305480         5.344436         2.674903   
1         4.441102         3.975107         1.000240         2.870631   
2        14.196937         5.708701        -0.753271        -5.627993   
3        17.296456         6.335396        -4.008689        -8.589818   
4        -3.418883         9.222596        21.236168        28.245889   

   eeg_signal_1247  eeg_signal_1248  eeg_signal_1249  eeg_signal_1250  
0        -0.055816        -1.212385        -2.461937        -4.930397  
1         7.071897         7.848365         4.033517        -2.110046  
2        -9.804085       -12.863908       -11.951175        -5.531799  
3        -5.876062         0.166707         6.054539        12.086351  
4        27.024864        17.794644         7.602379        -4.548318  

[5 rows x 251 columns]

In [7]:
#using Fourrier decomposition
n_fft=64
newcolumns = ['fft_2_sec_%s'%(i) for i in range(0,n_fft)]
df_train_final[newcolumns]=df_train.loc[:, 'eeg_signal_1000':].apply(lambda x: pd.Series(np.abs(np.fft.fft(x, n=n_fft, axis=-1, norm=None))), axis=1)

In [8]:
df_train_final.to_hdf('df_train_final.h5', key='df_train_final')

In [101]:
model='entropy_fft'
predictors = equations[model]['predictors']

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

0.507452988839627

In [115]:
model='entropy_fft_2_sec'
predictors = equations[model]['predictors']

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

0.5088671456963767

In [30]:
model = 'fft_2_sec_wavelets'
predictors = equations[model]['predictors']

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

0.5174285277480507

In [13]:
model = 'fft_fft_2_sec_wavelets'
predictors = equations[model]['predictors']

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

0.5183075982265709

## Focus sur la wavelet transform des 2 dernières secondes

In [9]:
def calculate_entropy(list_values):
    counter_values = Counter(list_values).most_common()
    probabilities = [elem[1]/len(list_values) for elem in counter_values]
    entropy=scipy.stats.entropy(probabilities)
    return entropy
 
def calculate_statistics(list_values):
    n5 = np.nanpercentile(list_values, 5)
    n25 = np.nanpercentile(list_values, 25)
    n75 = np.nanpercentile(list_values, 75)
    n95 = np.nanpercentile(list_values, 95)
    median = np.nanpercentile(list_values, 50)
    mean = np.nanmean(list_values)
    std = np.nanstd(list_values)
    var = np.nanvar(list_values)
    rms = np.nanmean(np.sqrt(list_values**2))
    return [n5, n25, n75, n95, median, mean, std, var, rms]
 
def calculate_crossings(list_values):
    zero_crossing_indices = np.nonzero(np.diff(np.array(list_values) > 0))[0]
    no_zero_crossings = len(zero_crossing_indices)
    mean_crossing_indices = np.nonzero(np.diff(np.array(list_values) > np.nanmean(list_values)))[0]
    no_mean_crossings = len(mean_crossing_indices)
    return [no_zero_crossings, no_mean_crossings]
 
def get_features(list_values):
    entropy = calculate_entropy(list_values)
    crossings = calculate_crossings(list_values)
    statistics = calculate_statistics(list_values)
    return [entropy] + crossings + statistics

In [10]:
def get_wawelet_features(dataset, waveletname):
    wawelet_features = []
    for signal_no in range(0, len(dataset)):
        features = []
        signal = dataset.loc[signal_no, :]
        list_coeff = pywt.wavedec(signal, waveletname)
        for coeff in list_coeff:
            features += get_features(coeff)
            
        wawelet_features.append(features)
    X = pd.DataFrame(wawelet_features)
    return X

In [11]:
wawelets=get_wawelet_features(df_train.loc[:, 'eeg_signal_1000':],"db5")

In [12]:
waweletscolumns = ['wawelets_2_sec_%s'%(i) for i in range(0, len(wawelets.columns))]
wawelets.columns=waweletscolumns

In [13]:
df_train_final=pd.concat([df_train_final,wawelets],axis=1)
df_train_final.head()

num_pso  mean_amp_pso  mean_dur_pso     amp_cso  dur_cso  time_since_sleep  \
0    237.0    152.658761    341.523207  128.017491    429.0           11379.0   
1    176.0    146.883435    338.039773  119.130849    196.0            6721.0   
2    456.0    152.376541    335.629386  164.292580    417.0           26832.0   
3     21.0    139.720772    336.285714  159.237082    407.0            1289.0   
4     72.0    140.649432    349.875000  130.184278    297.0            2262.0   

   time_in_ds  time_in_ls  time_in_rs  time_in_ws  ...  wawelets_2_sec_50  \
0      2730.0      3780.0         0.0       480.0  ...                 93   
1      2580.0      2100.0         0.0       480.0  ...                 90   
2      3240.0      7440.0      2130.0       750.0  ...                 96   
3         0.0        60.0         0.0       450.0  ...                 82   
4       630.0       960.0         0.0       450.0  ...                 89   

   wawelets_2_sec_51  wawelets_2_sec_52  wawelets_2_sec_53  wawelets_2_sec_54  \
0          -1.269829          -0.505228           0.505317           1.257482   
1          -1.251475          -0.580705           0.453012           1.541071   
2          -1.546928          -0.654804           0.599300           1.511609   
3          -1.446389          -0.538793           0.524387           1.378819   
4          -1.522254          -0.573445           0.530961           1.567218   

   wawelets_2_sec_55  wawelets_2_sec_56  wawelets_2_sec_57  wawelets_2_sec_58  \
0          -0.019131           0.001756           0.841372           0.707907   
1          -0.058753          -0.000819           0.852977           0.727571   
2           0.086784           0.006449           0.988418           0.976971   
3          -0.017170          -0.005554           0.886979           0.786731   
4           0.034848           0.005318           0.946961           0.896734   

   wawelets_2_sec_59  
0           0.660160  
1           0.658971  
2           0.774067  
3           0.691827  
4           0.718545  

[5 rows x 306 columns]

In [14]:
df_train_final.to_hdf('df_train_final.h5', key='df_train_final')

In [36]:
model='wawelets_2_sec'
predictors = equations[model]['predictors']

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

0.513530041278092

In [37]:
model='wavelets_wavelets_2_sec'
predictors = equations[model]['predictors']

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

0.5176578504815778

In [38]:
model='fft_wawelets_2_sec'
predictors = equations[model]['predictors']

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

0.5140651276563216

In [39]:
model='fft_2_sec_wawelets_2_sec'
predictors = equations[model]['predictors']

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

0.5138358049227947

In [40]:
model='fft_fft_2_sec_wawelets_2_sec'
predictors = equations[model]['predictors']

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

0.5145237731233756

In [42]:
model = 'fft_fft_2_sec_wawelets_wawelets_2_sec'
predictors = equations[model]['predictors']

dtrain = xgb.DMatrix(data=X_train[predictors], label=y_train)
dval = xgb.DMatrix(data=X_val[predictors])
params = {
    'max_depth': 7,
    'objective': 'multi:softmax',  # error evaluation for multiclass training
    'num_class': 3,
    'lambda': 0.1
}

bst = xgb.train(params, dtrain)
y_pred = bst.predict(dval)
accuracy_score(y_val, y_pred)

0.5180018345818682